# (Extract part) ETL: Cómo obtener todos los datos de todos los restaurantes en Rappi

En síntesis, este notebook es el primero de 3 que explican cómo obtener en .csv:
<ol>
<li>Los países disponibles en Rappi: paises_rappi.csv</li>
<li>Los cadenas de restaurantes disponibles en cada país: cadenas_restaurantes_df.csv</li>
<li>Las sucursales de cada cadena junto con sus atributos.</li>
<li>Una tabla aparte listando las opiniones ligadas a cada sucursal: opiniones_sucursales.csv</li>
</ol>
------
Nota: Si decides ejecutar este código:
<ol>
<li>Instala las librerías listadas en requirements.txt</li>
<li>Este código utiliza web scraping (Podría relantizar tu conexión a Internet.)</li>
<li>Ten en cuenta que se usa multiprocessing para acelerar ciertas partes del ETL (Podría relantizar tu máquina.)</li>
<li>Ligado al punto anterior, Estas mismas partes me demoraron entre 2 y 4 horas a terminar (Mi CPU tiene 4 cores y tengo una conexión de 230 megas/s).</li>
</ol>
Fecha de edición: 4/12/2022


## Obtenemos paises_rappi.csv

Importamos las librerías a utilizar durante esta parte del proyecto:

In [80]:
import concurrent.futures
import pandas as pd
import numpy as np
from bs4 import BeautifulSoup
import requests
import csv
import re

Debido a que usaremos scrapping con requests, definamos una pequeña función que corrobore si la conexión se logró o surgió un error y, de estar todo okey, nos retorne la sopa.

In [2]:
def obtener_sopa(url):
    url_request = requests.get(url)
    if url_request.status_code == 200:
        print('No problem status. Obteniendo sopa')
        soup = BeautifulSoup(url_request.text, 'lxml')
        print("Sopa obtenida")
        return soup
    else:
        status = f'Hubo un problema con la url: {url}'
        print(status)
        return None

A la fecha de esta edición, Rappi tiene todas las url's de cada país listadas en su footer. Con esto en mente obtendremos la etiqueta de los elementos que contienen los href's y los nombres de cada país.

In [42]:
# Definamos la url base
url_main = "https://www.rappi.com"
# Hacemos el request, verificamos status y obtenemos sopa
sopa = obtener_sopa(url_main) 

No problem status. Obteniendo sopa
Sopa obtenida


Para listar todos los países de Rappi actualmente:
1) Encontraremos el elemento con tag *ul* y id *1* que lista justo lo que necesitamos, a este le llamaremos *elemento_clave*.
2) Luego obtendremos todos los elementos con etiqueta *a* dentro de *elemento_clave*. (En está etiqueta están las url's y los nombres de cada país)
2) Luego listaremos cada url y cada nombre de cada país en *paises_url* y *paises_nombres*
3) Imprimimos resultados

In [28]:
elemento_clave = soup.find('ul', id="1") # Primer paso
elementos_a = elemento_clave.find_all('a') # Segundo paso
paises_url = [elementos_a[i].get('href') for i in range(len(elementos_a))] # Tercer paso
paises_nombres = [elementos_a[i].text for i in range(len(elementos_a))] # Sus nombres
paises_url # Ya adivinaste jaajaj

['https://www.rappi.com.ar/',
 'https://www.rappi.com.br/',
 'https://www.rappi.cl/',
 'https://www.rappi.com.co/',
 'https://www.rappi.co.cr/',
 'https://www.rappi.com.ec/',
 'https://www.rappi.com.mx/',
 'https://www.rappi.com.pe/',
 'https://www.rappi.com.uy/']

Listamos nuestros datos como df para exportarlo a .csv después

In [30]:
# Creamos el DF
paises_df = pd.DataFrame({"url_paises": paises_url, "nombre_pais": paises_nombres})
# Revisemos su estado
paises_df.head(3)

url_paises nombre_pais
0  https://www.rappi.com.ar/   Argentina
1  https://www.rappi.com.br/      Brasil
2      https://www.rappi.cl/       Chile

Ahora, a la fecha de esta edición, listaremos el tipo de cambio en doláres para cada moneda latinoamericana. (Esto nos servirá para convertir los precios de cada catálogo en una sola currency).

In [32]:
# Creamos la columna de intercambio de equivalencia a 1000 dólares.
equivalente_10000_dolares = [
    1676508,# Argentina
    52195,# Brasil
    8835000,# Chile
    47680700,# Colombia
    5981305, # Costa rica
    10000, # Ecuador
    193914,# Mexico
    38223.49,# Perú
    394049.80 # Uruguay
]
paises_df["1000_dollars_exchange"] = equivalente_10000_dolares
# Revisemos su estado
paises_df.head(3)

url_paises nombre_pais  1000_dollars_exchange
0  https://www.rappi.com.ar/   Argentina              1676508.0
1  https://www.rappi.com.br/      Brasil                52195.0
2      https://www.rappi.cl/       Chile              8835000.0

Listo. Ahora solo exportamos y guardamos el .csv

In [33]:
paises_df.to_csv("paises_rappi.csv", index_label="id_pais")

## Obteniendo cadenas_restaurantes_df.csv

<p>Para nuestra suerte, Rappi ya ha indexado cada cadena de restaurantes de cada país en un solo catálogo. El mismo dividido en distintas páginas (de la A hasta la Z junto con las cadenas que empiezan con números).
<p>Para acceder a este, solo se debe agregar "/catalogo/restaurants/a-1" a la url de cada país.
<p>Ejemplo, para Ecuador sería: "https://www.rappi.com.ec/catalogo/restaurants/a-a1".

Para lograr nuestro objetivo realizaremos 2 cosas:
1) Listar todas las subpáginas de cada catálogo de cada país.
2) Obtener los nombres y url's de cada cadena de cada subpágina.

Para esto necesitaremos nuestro df de países.

In [34]:
paises_df = pd.read_csv("paises_rappi.csv")

### Listar todas las subpáginas de cada catálogo de cada país.

In [55]:
# Nuestra url base
url_inicial_catalogo = "/catalogo/restaurants/a-1"
id_pais_subcatalogos_all = []
urls_catalogos_all = []
for i in paises_df.index:
    url_pais_elegido = paises_df.url_paises[i][:-1] #Obtenemos la url de cada país quitando 
                                                    # -el último '/'
    url_catalogo_pais = url_pais_elegido + url_inicial_catalogo
    try:
        catalogo_soup = obtener_sopa(url_catalogo_pais) # Obtenemos la sopa
        if sopa != None: # Si no hubo ningun problema al obtener la sopa
            # Obtenemos todos los subcatálogos
            paginas_catalogo = catalogo_soup.find_all(class_="sc-39328323-1 jiuMaW")
            # Obtenemos cada url de cada subcatálogo y lo concatenamos todo
            urls_subcatalogos = urls_catalogos_all + [url_pais_elegido + paginas_catalogo[j].get("href")
                                                      for j
                                                      in range(len(paginas_catalogo))]
            # Igualmente con el id del país correspondiente
            id_pais_subcatalogos = id_pais_subcatalogos_all + [i
                                                               for j
                                                               in range(len(urls_subcatalogos))]
    except:
        print(f"No se pudo obtener el catalogo de: {url_catalogo_pais}")
        continue
    print(f"Porcentaje completado: {round((i+1)*100 / len(paises_df.index), 2)}")
print("Terminado")

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 11.11
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 22.22
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 33.33
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 44.44
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 55.56
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 66.67
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 77.78
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 88.89
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 100.0
Terminado


In [66]:
# Creamos el DF
subcatalogos_df = pd.DataFrame({"url_subcatalogos": urls_catalogos_all, "id_pais": id_pais_subcatalogos_all})
# Revisemos su estado
subcatalogos_df.head(3)

url_subcatalogos  id_pais
0  https://www.rappi.com.ar/catalogo/restaurants/b-1        0
1  https://www.rappi.com.ar/catalogo/restaurants/c-1        0
2  https://www.rappi.com.ar/catalogo/restaurants/d-1        0

In [67]:
subcatalogos_df.to_csv("subcatalogos.csv",index_label="id_subcatalogo")

### Obtener los nombres y url's de cada cadena de cada subpágina.
Para esto usaremos las url's obtenidas anteriormente.

In [5]:
subcatalogos_df = pd.read_csv("subcatalogos.csv")
# Revisamos su estado
subcatalogos_df.head(3)

id_subcatalogo                                   url_subcatalogos  id_pais
0               0  https://www.rappi.com.ar/catalogo/restaurants/b-1        0
1               1  https://www.rappi.com.ar/catalogo/restaurants/c-1        0
2               2  https://www.rappi.com.ar/catalogo/restaurants/d-1        0

<p>En la interfaz encontramos que las *urls* y los *nombres* de los restaurantes podemos obtenerlos mediante la clase "sc-bdfBQB eXopiF sc-iqHYmW gcZftM secondary". Con esto en mente corremos el siguiente código:</p>
---------
<p>Nota: A partir de aquí utilizaremos multiprocessing para acelerar las cosas, de modo que dejaremos de agrupar nuestros datos en columnas sino en filas</p>

In [19]:
problema_url = []
def proccess_subcatalogos(index_to_process):
    i = index_to_process
    url_cadena_resturantes = []
    nombre_cadena_resturantes = []
    id_pais = []
    
    url_subcatalogo = subcatalogos_df.url_subcatalogos[i] # Obtenemos la url
    sub_id_pais = subcatalogos_df.id_pais[i] # Además del id del país
    sopa = obtener_sopa(url_subcatalogo) # Obtenemos la sopa
    # Trabajamos la sopa
    try:
        if sopa != None: # Si no hubo ningun problema al obtener la sopa
            # Obtenemos todos los nombres y urls y las concatenamos
            elementos_cadena_resturantes = sopa.find_all(class_="sc-bdfBQB eXopiF sc-iqHYmW gcZftM secondary")
            url_cadena_resturantes = url_cadena_resturantes + [elementos_cadena_resturantes[j].get("href")
                                                              for j
                                                              in range(len(elementos_cadena_resturantes))]
            nombre_cadena_resturantes = nombre_cadena_resturantes + [elementos_cadena_resturantes[j].find_all("span")[0].text
                                                                     for j 
                                                                    in range(len(elementos_cadena_resturantes))]
            # Luego guardamos el id del país correspondiente
            id_pais = id_pais + [sub_id_pais
                               for j
                               in range(len(nombre_cadena_resturantes))]
    except:
        print(f"No se pudo las sucursales en: {url_subcatalogo}")
        problema_url.append(url_subcatalogo)
    print(f"Porcentaje completado: {round((i+1)*100 / len(subcatalogos_df.index), 2)}")
    return (url_cadena_resturantes, nombre_cadena_resturantes, id_pais)

In [11]:
# Aquí usamos concurrent y multiproccesing para acelerar nuestro tiempo
all_index_subcatalogos = subcatalogos_df.index
# Obtenemos los datos
with concurrent.futures.ProcessPoolExecutor() as executor:
    results = executor.map(proccess_subcatalogos, all_index_subcatalogos)
# Guardamos nuestra data
data = list(results)

No problem status. Obteniendo sopaNo problem status. Obteniendo sopa

No problem status. Obteniendo sopaNo problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida

Porcentaje completado: 0.44
Terminado
Sopa obtenidaPorcentaje completado: 0.89

Porcentaje completado: 1.33
Terminado
Terminado
Sopa obtenida
Porcentaje completado: 1.78
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.22
Terminado
No problem status. Obteniendo sopa
No problem status. Obteniendo sopaNo problem status. Obteniendo sopaSopa obtenida


Sopa obtenida
Porcentaje completado: 3.56Porcentaje completado: 3.11Sopa obtenida


Porcentaje completado: 2.67Terminado

Terminado
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 4.0
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 4.44No problem status. Obteniendo sopa

Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenidaPorcentaje completado: 4.89

Termi

Porcentaje completado: 83.11
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
No problem status. Obteniendo sopa
Porcentaje completado: 83.56
Terminado
Sopa obtenida
Porcentaje completado: 84.0
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 84.44
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 84.89
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 85.33
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 85.78
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 86.22
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 86.67
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 87.11
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 87.56
Terminado
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 88.0
Termi

Revisamos si obtuvimos algún error en alguna url

In [31]:
problema_url

[]

Cool, ninguno. Ahora nuestra series están guardadas en subtuplas de sublistas de la lista data. Para poder utilizarla tenemos que descomprimir estas tuplas y luego concatenarlas

In [17]:
# Creamos pd.Series vacías para usarlas en la concatenación
url_cadena_resturantes = pd.Series([], dtype=str)
nombre_cadena_resturantes = pd.Series([], dtype=str)
id_pais = pd.Series([], dtype="int64")

# Concatenamos cada lista con su respectiva serie
for tuplita in data:
    url_cadena_resturantes_next = pd.Series(tuplita[0])
    url_cadena_resturantes = pd.concat([url_cadena_resturantes_next,url_cadena_resturantes])
    
    nombre_cadena_resturantes_next = pd.Series(tuplita[1])
    nombre_cadena_resturantes = pd.concat([nombre_cadena_resturantes_next,nombre_cadena_resturantes])
    
    id_pais_next = pd.Series(tuplita[2])
    id_pais = pd.concat([id_pais_next,id_pais])

Cool, todo okey. Ahora veamos como quedo:

In [20]:
cadenas_restaurantes_df = pd.DataFrame({"nombre_cadena": nombre_cadena_resturantes,
                                       "url_cadena": url_cadena_resturantes,
                                       "id_pais": id_pais})
# Lo revisamos
cadenas_restaurantes_df.head(3)

nombre_cadena                                         url_cadena  id_pais
0        Zoubar  https://www.rappi.com.uy/restaurantes/delivery...        8
0  Yuppy Burger  https://www.rappi.com.uy/restaurantes/delivery...        8
0    Wok in Box  https://www.rappi.com.uy/restaurantes/delivery...        8

In [26]:
# Reseteamos el índice
cadenas_restaurantes_df.reset_index(drop=True, inplace=True)
# Veamos como queda finalmente
cadenas_restaurantes_df.head(3)

nombre_cadena                                         url_cadena  id_pais
0        Zoubar  https://www.rappi.com.uy/restaurantes/delivery...        8
1  Yuppy Burger  https://www.rappi.com.uy/restaurantes/delivery...        8
2    Wok in Box  https://www.rappi.com.uy/restaurantes/delivery...        8

In [29]:
# Guardamos nuestro trabajo
cadenas_restaurantes_df.to_csv("cadenas_restaurantes.csv", index_label="id_cadena")

## Sucursales: Obteniendo todas las sucursales de cada cadena

Cool, a 1 paso de completar nuestra extracción. Ahora, en cada cadena de restaurantes existen diferentes sucursales y cada una de ellas con un nombre, una url y una dirección únicas).
Ahora tocaría:
1) Aplicar la misma idea del paso anterior pero para cada sucursal.

In [4]:
# Importamos nuestro trabajo anterior
cadenas_restaurantes_df = pd.read_csv("cadenas_restaurantes.csv") 
# Lo revisamos
cadenas_restaurantes_df.head(3) 

id_cadena nombre_cadena                                         url_cadena  \
0          0        Zoubar  https://www.rappi.com.uy/restaurantes/delivery...   
1          1  Yuppy Burger  https://www.rappi.com.uy/restaurantes/delivery...   
2          2    Wok in Box  https://www.rappi.com.uy/restaurantes/delivery...   

   id_pais  
0        8  
1        8  
2        8

In [40]:
problema_url = []
no_hay_sucursales_url = []
def proccess_sucursales(index_to_process):
    i = index_to_process
    url_sucursales = []
    nombre_sucursales = []
    direccion_sucursales = []
    id_cadena = []
    
    url_cadena_elegida = cadenas_restaurantes_df.url_cadena[i] # Obtenemos la url
    sub_id_cadena = cadenas_restaurantes_df.id_cadena[i] # Además del id del país
    sopa = obtener_sopa(url_cadena_elegida) # Obtenemos la sopa
    # Trabajamos la sopa
    try:
        if sopa != None: # Si no hubo ningun problema al obtener la sopa
            div_sucursales = sopa.find("div",
                              {'data-testid': 'topRestCard'},
                              class_="sc-9fb51c13-6 fIgfiC"
                              )
            try:
                sucursales = div_sucursales.find_all("a")
                # Obtenemos todos los nombres y urls y las concatenamos
                url_pais_base = re.split("/restaurantes" , url_cadena_elegida)[0]
                # Obtenemos los atributos de cada sucursal
                url_sucursales = url_sucursales + [url_pais_base + sucursales[i].get("href")
                                                   for i
                                                   in range(len(sucursales))]
                nombre_sucursales = nombre_sucursales + [sucursales[i].find_all("h3")[0].text
                                                        for i
                                                         in range(len(sucursales))]
                direccion_sucursales = direccion_sucursales + [sucursales[i].find_all("div", class_="sc-bxivhb fFeDyp sc-d9669f19-7 iOdleX")[0].text
                                                               for i
                                                               in range(len(sucursales))]
                # Luego guardamos el id del país correspondiente
                id_cadena = id_cadena + [sub_id_cadena
                                   for j
                                   in range(len(nombre_sucursales))]
            except:
                print(f"No hay sucursales en la url {url_cadena_elegida}.")
                no_hay_sucursales_url.append(url_cadena_elegida)
    except:
        print(f"No se pudo ingresar a: {url_cadena_elegida}")
        problema_url.append(url_cadena_elegida)
    print(f"Porcentaje completado: {round((i+1)*100 / len(cadenas_restaurantes_df.index), 2)}")
    return (url_sucursales, nombre_sucursales, direccion_sucursales, id_cadena)

In [42]:
# Aplicamos multiproccesing
all_index_subcatalogos = cadenas_restaurantes_df.index
# Obtenemos los datos
with concurrent.futures.ProcessPoolExecutor() as executor:
    results = executor.map(proccess_sucursales, all_index_subcatalogos)
# Guardamos nuestra data
data = list(results)

No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
No problem status. Obteniendo sopaSopa obtenida

No problem status. Obteniendo sopaPorcentaje completado: 0.02
Sopa obtenida

Sopa obtenida
Porcentaje completado: 0.01Porcentaje completado: 0.03Sopa obtenida


Porcentaje completado: 0.02
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.04
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.05Sopa obtenida

Porcentaje completado: 0.06
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.07
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.08
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.08
Sopa obtenida
No hay sucursales en la url https://www.rappi.com.uy/restaurantes/delivery/10045-welcome-burgers.
Porcentaje completado: 0.05
No problem status. Obteniendo sopa
Sopa obtenida
Porcen

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.79
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.81
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.82
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.83
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.84
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.86
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.85
Sopa obtenida
No hay sucursales en la url https://www.rappi.com.uy/restaurantes/delivery/6763-empanada-de-la-mancha.
Porcentaje completado: 0.82
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.86
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.87
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.88
No problem status. Obteniendo sopa
Sopa obtenida
P

Porcentaje completado: 1.59
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 1.61
Sopa obtenida
Porcentaje completado: 1.6
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 1.6
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 1.62
No problem status. Obteniendo sopa
Sopa obtenida
No problem status. Obteniendo sopaPorcentaje completado: 1.63

Sopa obtenida
Porcentaje completado: 1.63
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 1.64
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 1.65
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 1.66
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 1.67
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 1.69
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 1.66
No problem status. Obteniendo sopa
Sopa obtenida
P

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.41
Sopa obtenida
Porcentaje completado: 2.39
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.4
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.41
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.42
Sopa obtenida
Porcentaje completado: 2.44
Sopa obtenida
Porcentaje completado: 2.43
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.44
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.45
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.46
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.47
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.48
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 2.49


No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.21
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.21
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.23
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.22
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.24
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.25
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.25
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.27
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.26
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.28
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.28
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.29
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.3


...

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.27
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.27
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.28
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.29
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.3
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.31
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.33
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.32
Sopa obtenida
No hay sucursales en la url https://www.rappi.com.ar/restaurantes/delivery/24645-fortnit-burger.
Porcentaje completado: 96.3
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.34
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 96.34
No problem status. Obteniendo sopa
Sopa obtenid

No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.05
Sopa obtenida
Porcentaje completado: 97.04
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.05
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.06
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.08
Sopa obtenida
Porcentaje completado: 97.07
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.08
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.09
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.1No problem status. Obteniendo sopa

Sopa obtenida
Porcentaje completado: 97.11
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.11
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.12
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje compl

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.84
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.83
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.85
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.85
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.86
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.87
Sopa obtenida
Porcentaje completado: 97.88
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.89
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.89
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.9
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.91
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 97.92
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje compl

Porcentaje completado: 98.61
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.62
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.63
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.64
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.63
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.65
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.66
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.66
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.67
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.69
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.68
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 98.69
Sopa obtenida
Porcentaje completado: 98.7
No problem status. Obteniendo sopa
S

Sopa obtenida
Porcentaje completado: 99.4
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.41
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.43
Sopa obtenida
Porcentaje completado: 99.42
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.43
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.44
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.45
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.47
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.47
No problem status. Obteniendo sopa
Sopa obtenida
No hay sucursales en la url https://www.rappi.com.ar/restaurantes/delivery/11739-buenos-aires-fried-chicken.
Porcentaje completado: 99.46
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenidaPorcentaje completado: 99.49

Porcentaje completad

Revisamos si obtuvimos algún error en alguna url

In [43]:
print(f"Problemas encontrados urls: {len(problema_url)}")
print(f"Cadenas sin sucursal: {len(no_hay_sucursales_url)}")

Problemas encontrados urls: 0
Cadenas sin sucursal: 0


En este caso nos lista que no hay errores, esto sucede porque no he puesto las variables en global de modo que sucede esto. Pero como pudimos ver en el Output, sí hay cadenas que o no tienen sucursales disponibles o no se pudo acceder a estas mismas. Por el momento lo dejaremos pasar.

In [44]:
# Creamos pd.Series vacías para usarlas en la concatenación
url_sucursal = pd.Series([], dtype=str)
nombre_sucursal = pd.Series([], dtype=str)
direccion_sucursal = pd.Series([], dtype=str)
id_cadena = pd.Series([], dtype="int64")

# Concatenamos cada lista con su respectiva serie
for i, tuplita in enumerate(data):
    url_sucursal_next = pd.Series(tuplita[0], dtype=str)
    url_sucursal = pd.concat([url_sucursal_next,url_sucursal])
    
    nombre_sucursal_next = pd.Series(tuplita[1], dtype=str)
    nombre_sucursal = pd.concat([nombre_sucursal_next,nombre_sucursal])
    
    direccion_sucursal_next = pd.Series(tuplita[2], dtype=str)
    direccion_sucursal = pd.concat([direccion_sucursal_next, direccion_sucursal])
    
    id_cadena_next = pd.Series(tuplita[3], dtype="int64")
    id_cadena = pd.concat([id_cadena_next,id_cadena])
    
    print(f"Porcentaje completado: {round((i+1)*100 / len(data), 2)}")

Porcentaje completado: 0.01
Porcentaje completado: 0.02
Porcentaje completado: 0.02
Porcentaje completado: 0.03
Porcentaje completado: 0.04
Porcentaje completado: 0.05
Porcentaje completado: 0.05
Porcentaje completado: 0.06
Porcentaje completado: 0.07
Porcentaje completado: 0.08
Porcentaje completado: 0.08
Porcentaje completado: 0.09
Porcentaje completado: 0.1
Porcentaje completado: 0.11
Porcentaje completado: 0.11
Porcentaje completado: 0.12
Porcentaje completado: 0.13
Porcentaje completado: 0.14
Porcentaje completado: 0.15
Porcentaje completado: 0.15
Porcentaje completado: 0.16
Porcentaje completado: 0.17
Porcentaje completado: 0.18
Porcentaje completado: 0.18
Porcentaje completado: 0.19
Porcentaje completado: 0.2
Porcentaje completado: 0.21
Porcentaje completado: 0.21
Porcentaje completado: 0.22
Porcentaje completado: 0.23
Porcentaje completado: 0.24
Porcentaje completado: 0.24
Porcentaje completado: 0.25
Porcentaje completado: 0.26
Porcentaje completado: 0.27
Porcentaje completado:

Porcentaje completado: 4.02
Porcentaje completado: 4.03
Porcentaje completado: 4.04
Porcentaje completado: 4.05
Porcentaje completado: 4.05
Porcentaje completado: 4.06
Porcentaje completado: 4.07
Porcentaje completado: 4.08
Porcentaje completado: 4.08
Porcentaje completado: 4.09
Porcentaje completado: 4.1
Porcentaje completado: 4.11
Porcentaje completado: 4.12
Porcentaje completado: 4.12
Porcentaje completado: 4.13
Porcentaje completado: 4.14
Porcentaje completado: 4.15
Porcentaje completado: 4.15
Porcentaje completado: 4.16
Porcentaje completado: 4.17
Porcentaje completado: 4.18
Porcentaje completado: 4.18
Porcentaje completado: 4.19
Porcentaje completado: 4.2
Porcentaje completado: 4.21
Porcentaje completado: 4.21
Porcentaje completado: 4.22
Porcentaje completado: 4.23
Porcentaje completado: 4.24
Porcentaje completado: 4.25
Porcentaje completado: 4.25
Porcentaje completado: 4.26
Porcentaje completado: 4.27
Porcentaje completado: 4.28
Porcentaje completado: 4.28
Porcentaje completado:

Porcentaje completado: 7.74
Porcentaje completado: 7.75
Porcentaje completado: 7.76
Porcentaje completado: 7.77
Porcentaje completado: 7.77
Porcentaje completado: 7.78
Porcentaje completado: 7.79
Porcentaje completado: 7.8
Porcentaje completado: 7.8
Porcentaje completado: 7.81
Porcentaje completado: 7.82
Porcentaje completado: 7.83
Porcentaje completado: 7.83
Porcentaje completado: 7.84
Porcentaje completado: 7.85
Porcentaje completado: 7.86
Porcentaje completado: 7.86
Porcentaje completado: 7.87
Porcentaje completado: 7.88
Porcentaje completado: 7.89
Porcentaje completado: 7.89
Porcentaje completado: 7.9
Porcentaje completado: 7.91
Porcentaje completado: 7.92
Porcentaje completado: 7.93
Porcentaje completado: 7.93
Porcentaje completado: 7.94
Porcentaje completado: 7.95
Porcentaje completado: 7.96
Porcentaje completado: 7.96
Porcentaje completado: 7.97
Porcentaje completado: 7.98
Porcentaje completado: 7.99
Porcentaje completado: 7.99
Porcentaje completado: 8.0
Porcentaje completado: 8

Porcentaje completado: 10.87
Porcentaje completado: 10.88
Porcentaje completado: 10.89
Porcentaje completado: 10.9
Porcentaje completado: 10.9
Porcentaje completado: 10.91
Porcentaje completado: 10.92
Porcentaje completado: 10.93
Porcentaje completado: 10.93
Porcentaje completado: 10.94
Porcentaje completado: 10.95
Porcentaje completado: 10.96
Porcentaje completado: 10.96
Porcentaje completado: 10.97
Porcentaje completado: 10.98
Porcentaje completado: 10.99
Porcentaje completado: 10.99
Porcentaje completado: 11.0
Porcentaje completado: 11.01
Porcentaje completado: 11.02
Porcentaje completado: 11.03
Porcentaje completado: 11.03
Porcentaje completado: 11.04
Porcentaje completado: 11.05
Porcentaje completado: 11.06
Porcentaje completado: 11.06
Porcentaje completado: 11.07
Porcentaje completado: 11.08
Porcentaje completado: 11.09
Porcentaje completado: 11.09
Porcentaje completado: 11.1
Porcentaje completado: 11.11
Porcentaje completado: 11.12
Porcentaje completado: 11.12
Porcentaje complet

Porcentaje completado: 13.84
Porcentaje completado: 13.84
Porcentaje completado: 13.85
Porcentaje completado: 13.86
Porcentaje completado: 13.87
Porcentaje completado: 13.87
Porcentaje completado: 13.88
Porcentaje completado: 13.89
Porcentaje completado: 13.9
Porcentaje completado: 13.9
Porcentaje completado: 13.91
Porcentaje completado: 13.92
Porcentaje completado: 13.93
Porcentaje completado: 13.93
Porcentaje completado: 13.94
Porcentaje completado: 13.95
Porcentaje completado: 13.96
Porcentaje completado: 13.97
Porcentaje completado: 13.97
Porcentaje completado: 13.98
Porcentaje completado: 13.99
Porcentaje completado: 14.0
Porcentaje completado: 14.0
Porcentaje completado: 14.01
Porcentaje completado: 14.02
Porcentaje completado: 14.03
Porcentaje completado: 14.03
Porcentaje completado: 14.04
Porcentaje completado: 14.05
Porcentaje completado: 14.06
Porcentaje completado: 14.06
Porcentaje completado: 14.07
Porcentaje completado: 14.08
Porcentaje completado: 14.09
Porcentaje complet

...

Porcentaje completado: 90.65
Porcentaje completado: 90.65
Porcentaje completado: 90.66
Porcentaje completado: 90.67
Porcentaje completado: 90.68
Porcentaje completado: 90.68
Porcentaje completado: 90.69
Porcentaje completado: 90.7
Porcentaje completado: 90.71
Porcentaje completado: 90.72
Porcentaje completado: 90.72
Porcentaje completado: 90.73
Porcentaje completado: 90.74
Porcentaje completado: 90.75
Porcentaje completado: 90.75
Porcentaje completado: 90.76
Porcentaje completado: 90.77
Porcentaje completado: 90.78
Porcentaje completado: 90.78
Porcentaje completado: 90.79
Porcentaje completado: 90.8
Porcentaje completado: 90.81
Porcentaje completado: 90.81
Porcentaje completado: 90.82
Porcentaje completado: 90.83
Porcentaje completado: 90.84
Porcentaje completado: 90.85
Porcentaje completado: 90.85
Porcentaje completado: 90.86
Porcentaje completado: 90.87
Porcentaje completado: 90.88
Porcentaje completado: 90.88
Porcentaje completado: 90.89
Porcentaje completado: 90.9
Porcentaje comple

Porcentaje completado: 92.88
Porcentaje completado: 92.89
Porcentaje completado: 92.9
Porcentaje completado: 92.91
Porcentaje completado: 92.91
Porcentaje completado: 92.92
Porcentaje completado: 92.93
Porcentaje completado: 92.94
Porcentaje completado: 92.94
Porcentaje completado: 92.95
Porcentaje completado: 92.96
Porcentaje completado: 92.97
Porcentaje completado: 92.98
Porcentaje completado: 92.98
Porcentaje completado: 92.99
Porcentaje completado: 93.0
Porcentaje completado: 93.01
Porcentaje completado: 93.01
Porcentaje completado: 93.02
Porcentaje completado: 93.03
Porcentaje completado: 93.04
Porcentaje completado: 93.04
Porcentaje completado: 93.05
Porcentaje completado: 93.06
Porcentaje completado: 93.07
Porcentaje completado: 93.07
Porcentaje completado: 93.08
Porcentaje completado: 93.09
Porcentaje completado: 93.1
Porcentaje completado: 93.11
Porcentaje completado: 93.11
Porcentaje completado: 93.12
Porcentaje completado: 93.13
Porcentaje completado: 93.14
Porcentaje comple

Porcentaje completado: 95.27
Porcentaje completado: 95.27
Porcentaje completado: 95.28
Porcentaje completado: 95.29
Porcentaje completado: 95.3
Porcentaje completado: 95.3
Porcentaje completado: 95.31
Porcentaje completado: 95.32
Porcentaje completado: 95.33
Porcentaje completado: 95.33
Porcentaje completado: 95.34
Porcentaje completado: 95.35
Porcentaje completado: 95.36
Porcentaje completado: 95.37
Porcentaje completado: 95.37
Porcentaje completado: 95.38
Porcentaje completado: 95.39
Porcentaje completado: 95.4
Porcentaje completado: 95.4
Porcentaje completado: 95.41
Porcentaje completado: 95.42
Porcentaje completado: 95.43
Porcentaje completado: 95.43
Porcentaje completado: 95.44
Porcentaje completado: 95.45
Porcentaje completado: 95.46
Porcentaje completado: 95.46
Porcentaje completado: 95.47
Porcentaje completado: 95.48
Porcentaje completado: 95.49
Porcentaje completado: 95.5
Porcentaje completado: 95.5
Porcentaje completado: 95.51
Porcentaje completado: 95.52
Porcentaje completad

Porcentaje completado: 97.59
Porcentaje completado: 97.59
Porcentaje completado: 97.6
Porcentaje completado: 97.61
Porcentaje completado: 97.62
Porcentaje completado: 97.63
Porcentaje completado: 97.63
Porcentaje completado: 97.64
Porcentaje completado: 97.65
Porcentaje completado: 97.66
Porcentaje completado: 97.66
Porcentaje completado: 97.67
Porcentaje completado: 97.68
Porcentaje completado: 97.69
Porcentaje completado: 97.69
Porcentaje completado: 97.7
Porcentaje completado: 97.71
Porcentaje completado: 97.72
Porcentaje completado: 97.72
Porcentaje completado: 97.73
Porcentaje completado: 97.74
Porcentaje completado: 97.75
Porcentaje completado: 97.76
Porcentaje completado: 97.76
Porcentaje completado: 97.77
Porcentaje completado: 97.78
Porcentaje completado: 97.79
Porcentaje completado: 97.79
Porcentaje completado: 97.8
Porcentaje completado: 97.81
Porcentaje completado: 97.82
Porcentaje completado: 97.82
Porcentaje completado: 97.83
Porcentaje completado: 97.84
Porcentaje comple

Porcentaje completado: 99.88
Porcentaje completado: 99.89
Porcentaje completado: 99.89
Porcentaje completado: 99.9
Porcentaje completado: 99.91
Porcentaje completado: 99.92
Porcentaje completado: 99.92
Porcentaje completado: 99.93
Porcentaje completado: 99.94
Porcentaje completado: 99.95
Porcentaje completado: 99.95
Porcentaje completado: 99.96
Porcentaje completado: 99.97
Porcentaje completado: 99.98
Porcentaje completado: 99.98
Porcentaje completado: 99.99
Porcentaje completado: 100.0


Bueno, como podrás imaginarte, para este proposito también hay una clase y una etiqueta específica que revisar jaja

In [45]:
sucursales_df = pd.DataFrame({"id_cadena": id_cadena,
                              "url_sucursal": url_sucursal,
                              "nombre_sucursal": nombre_sucursal,
                             "direccion_sucursal": direccion_sucursal})
# Lo revisamos
sucursales_df.head(3)

id_cadena                                       url_sucursal  \
0      13096  https://www.rappi.com.ar/restaurantes/135367-b...   
0      13095  https://www.rappi.com.ar/restaurantes/135220-b...   
0      13094  https://www.rappi.com.ar/restaurantes/135040-b...   

        nombre_sucursal                                 direccion_sucursal  
0         Bulls Burgers  Av. Gral. San Martín 1397 1704 Ramos Mejía Pro...  
0          Bar La Docta                                       balcarce 365  
0  BA Bakery - Belgrano  Av Belgrano 265, Microcentro, Buenos Aires, Ar...

In [48]:
# Ordenamos en base a la id_cadena
sucursales_df = sucursales_df.sort_values("id_cadena", axis=0)
# Reseteamos el índice
sucursales_df.reset_index(drop=True, inplace=True)
# Veamos como queda finalmente
sucursales_df.head(3)

id_cadena                                       url_sucursal  \
0          0  https://www.rappi.com.uy/restaurantes/113198-z...   
1          1  https://www.rappi.com.uy/restaurantes/120305-y...   
2          2  https://www.rappi.com.uy/restaurantes/119128-w...   

         nombre_sucursal                                 direccion_sucursal  
0                 Zoubar                                 8 de Octubre 2698   
1           Yuppy Burger  Colonia 1779, Montevideo, Departamento de Mont...  
2  Wok in Box - Williman  Claudio Williman 626, 11300 Montevideo, Depart...

In [59]:
# Guardamos nuestro trabajo
sucursales_df.to_csv("sucursales.csv", index_label="id_sucursal")

Cool, todo bien. La única nota ha dejar es que existen algunas cadenas de comida a las que no se pudieron sacar sus sucursales. Esto se debe a que SÍ están indexadas en el directorio de Rappi pero NO tienen sucursales disponibles, se han dado de baja o por x razón no aparecen sus sucursales.

## Obteniendo las opiniones, precios y otros atributos de cada sucursal

Con esto ingresaremos a cada sucursal y obtendremos la siguiente información:
- Opiniones: Las opiniones y sus porcentajes de cada sucursal.
- Precios: Todos los precios de cada producto listado en el catálogo.
- Otros atributos: Número de calificaciones, estrellas promedio, tiempo de envío, etc.
----
En algunas no se tienen estos datos, así que tendremos que poner "No abierto al público / No calificado".

In [60]:
sucursales_df = pd.read_csv("sucursales.csv")
sucursales_df.head(3)

id_sucursal  id_cadena                                       url_sucursal  \
0            0          0  https://www.rappi.com.uy/restaurantes/113198-z...   
1            1          1  https://www.rappi.com.uy/restaurantes/120305-y...   
2            2          2  https://www.rappi.com.uy/restaurantes/119128-w...   

         nombre_sucursal                                 direccion_sucursal  
0                 Zoubar                                 8 de Octubre 2698   
1           Yuppy Burger  Colonia 1779, Montevideo, Departamento de Mont...  
2  Wok in Box - Williman  Claudio Williman 626, 11300 Montevideo, Depart...

Ahora obtenemos los datos que nos interesan. Probaremos con una sucursal

In [61]:
# Obtenemos la url de la sucursal de ejemplo
sucursal_url = sucursales_df.url_sucursal[3]
print(f"Obteniendo sopa de: {sucursal_url}")
# Obtenemos la sopa
sopa = obtener_sopa(sucursal_url)

Obteniendo sopa de: https://www.rappi.com.uy/restaurantes/120325-wok-in-box
No problem status. Obteniendo sopa
Sopa obtenida


In [81]:
# Usaremos una lambda para retornar "None" si no hay opiniones o las opiniones si sí las hay.
revisador_de_nonetypes = lambda element: np.nan if element == None else element.text
# Creamos nuestra función para obtener los atributos
def get_all_attr(soup_sucursal):
    try:
        # Obtenemos las estrellas y el número de opiniones
        overral_stars = revisador_de_nonetypes(soup_sucursal.find("span", class_="sc-bxivhb gJCKbU"))
        number_opinions = revisador_de_nonetypes(soup_sucursal.find("span", class_="sc-bxivhb dVvqfA")) # Le quitamos los parentesis
        tiempo_delivery = revisador_de_nonetypes(soup_sucursal.find("span", class_="sc-bxivhb ecrUmJ"))
        tipo_envio = revisador_de_nonetypes(soup_sucursal.find("div", class_="chakra-skeleton css-1vjr0v9"))
        if not pd.isna(number_opinions):
            number_opinions = int(number_opinions[1:-1]) # Para quitar los parentesis y obtener el número
        return [overral_stars, number_opinions, tiempo_delivery, tipo_envio]
    except:
        print("03 Problema al obtener atributos globales. Retornando error")
        error = "Problema atributos"
        return error
get_all_attr(sopa)

[nan, nan, nan, 'Gratis(nuevos usuarios)']

In [82]:
# Nuestra función para obtener todos los precios
def get_all_prices(soup_sucursal):
    try:
        # Encontrar lista de precios de productos
        div_prices_unparsed = soup_sucursal.find_all("span", class_="chakra-text css-kowr8")
        prices = [div_prices_unparsed[i].text
                        for i in range(len(div_prices_unparsed))]
        return prices
    except:
        print("02 Problema al obtener precios. Retornando error")
        prices = "Problema precios"
        return prices
get_all_prices(sopa)

['$ 1.150,00',
 '$ 1.200,00',
 '$ 1.250,00',
 '$ 250,00',
 '$ 395,00',
 '$ 450,00',
 '$ 450,00',
 '$ 450,00',
 '$ 450,00',
 '$ 450,00',
 '$ 490,00',
 '$ 490,00',
 '$ 490,00',
 '$ 490,00',
 '$ 490,00',
 '$ 490,00',
 '$ 490,00',
 '$ 490,00',
 '$ 490,00',
 '$ 90,00',
 '$ 90,00',
 '$ 90,00',
 '$ 120,00',
 '$ 240,00',
 '$ 120,00',
 '$ 90,00',
 '$ 90,00',
 '$ 90,00',
 '$ 90,00',
 '$ 180,00',
 '$ 120,00',
 '$ 120,00',
 '$ 100,00',
 '$ 100,00']

In [83]:
# Nuestra sopa para obtener las diferentes opiniones con su porcentaje
def get_all_opinions(soup_sucursal):
    try:
        div_opinions_unparsed = soup_sucursal.find_all("div", class_="css-z7mtfw")
        # Nos quedamos con los spans de cada opinion para tener su texto y porcentajes
        opinions_unparsed = [div_opinions_unparsed[i].find_all("span")
                        for i in range(len(div_opinions_unparsed))]
        # Agarramos el texto Y porcentajes
        opinions = [(opinions_unparsed[i][0].text, opinions_unparsed[i][1].text)
                    for i in range(len(opinions_unparsed))]
        return opinions
    except:
        print("01 Problema al obtener opiniones. Retornando error")
        opinions = "Error opiniones"
        return opinions
get_all_opinions(sopa) # Si retorna una lista vacía es que no se encontraron opiniones

[]

Con estos datos podemos empezar a obtener todos los metadatos de cada sucursal

In [84]:
problema_obtener_url = []
# Definición de nuestra función base
def process_sucursal(index_sucursal):
    i = index_sucursal
    sucursal_url = sucursales_df.url_sucursal[i]
    # Obtenemos el ID de la sucursal
    id_sucursal = sucursales_df.id_sucursal[i] 
    try:
        # Obtenemos la sopa
        sopa = obtener_sopa(sucursal_url)
        attributes = get_all_attr(sopa)
        prices = get_all_prices(sopa)
        opinions = get_all_opinions(sopa)
        print(f"Porcentaje completado: {round((i+1)*100 / len(sucursales_df.index), 2)}")
        return id_sucursal, attributes, prices, opinions
    except:
        try:
            # Obtenemos la sopa
            print("Intentando obtener sopa denuevo")
            sopa = obtener_sopa(sucursal_url)
            # Obtenemos todos los datos
            attributes = get_all_attr(sopa)
            prices = get_all_prices(sopa)
            opinions = get_all_opinions(sopa)
            print(f"Porcentaje completado: {round((i+1)*100 / len(sucursales_df.index), 2)}")
            return id_sucursal, attributes, prices, opinions
        except:
            print(f"Hubo un problema con la sopa de la url {url_sucursal_elegida}")
            problema_obtener_url.append(url_sucursal_elegida)

In [86]:
# Aquí usamos concurrent y multiproccesing para acelerar nuestro tiempo
all_index_sucursales = sucursales_df.index

with concurrent.futures.ProcessPoolExecutor() as executor:
    results = executor.map(process_sucursal, all_index_sucursales)
    
# Guardamos la data
data = list(results)

No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
No problem status. Obteniendo sopaNo problem status. Obteniendo sopa

Sopa obtenida
Sopa obtenida
Porcentaje completado: 0.0Sopa obtenidaSopa obtenida

Porcentaje completado: 0.01

Porcentaje completado: 0.0
Porcentaje completado: 0.01
No problem status. Obteniendo sopa
Sopa obtenida
No problem status. Obteniendo sopaPorcentaje completado: 0.01

Sopa obtenida
Porcentaje completado: 0.02
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.02
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.02
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.02
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.01
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.02
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.03
Sopa obtenida
Porcentaje completado: 0.03
N

Porcentaje completado: 0.24
Sopa obtenida
Sopa obtenida
Porcentaje completado: 0.24
Porcentaje completado: 0.24
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.25
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Porcentaje completado: 0.25
Porcentaje completado: 0.25
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Sopa obtenida
Porcentaje completado: 0.26
Porcentaje completado: 0.25
Porcentaje completado: 0.26
Sopa obtenida
Porcentaje completado: 0.24
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Porcentaje completado: 0.26
Porcentaje completado: 0.27
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenidaSopa obtenida

Porcentaje completado: 0.27Porcentaje completado: 0.27

No problem status. Obteniendo sopa
No pro

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.49
No problem status. Obteniendo sopa
Sopa obtenida
No problem status. Obteniendo sopa
Porcentaje completado: 0.48
Sopa obtenida
Porcentaje completado: 0.48
No problem status. Obteniendo sopa
Sopa obtenidaNo problem status. Obteniendo sopa

Porcentaje completado: 0.49
Sopa obtenida
Porcentaje completado: 0.49
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.49
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.5
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Porcentaje completado: 0.49Porcentaje completado: 0.5

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.5
No problem status. Obteniendo sopa
Sopa obtenida
No problem status. Obteniendo sopa
No problem status. Obteniendo sopaPorcentaje completado: 0.5

Sopa obtenida
Porcentaje completado: 0.51
Sopa obtenida
Porcentaje completado: 0.51
No 

Sopa obtenida
Porcentaje completado: 0.73
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Sopa obtenida
Porcentaje completado: 0.72Porcentaje completado: 0.72

Porcentaje completado: 0.71
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.73
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.73
Sopa obtenida
Porcentaje completado: 0.73
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.73
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.74
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.74
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.75
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.74
Sopa obtenida
Porcentaje completado: 0.75
No problem status. Obteniendo sopa

Porcentaje completado: 0.95
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.96
No problem status. Obteniendo sopa
Sopa obtenida
No problem status. Obteniendo sopaPorcentaje completado: 0.96

Sopa obtenida
Porcentaje completado: 0.97
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.96
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.97
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.97
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Porcentaje completado: 0.97Porcentaje completado: 0.97

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 0.98
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
No problem status. Obteniendo sopa
Porcentaje completado: 0.98
Sopa obtenida
Porcentaje completado: 0.98
Sopa obtenida
Porcentaje completado: 0.98
No problem status. Obteniendo sopa
Sopa obtenida

...

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.05
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.05
No problem status. Obteniendo sopa
Sopa obtenida
No problem status. Obteniendo sopa
Porcentaje completado: 99.05
Sopa obtenida
Porcentaje completado: 99.06
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.06
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.07
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.07
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenidaPorcentaje completado: 99.06

Porcentaje completado: 99.06
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Porcentaje completado: 99.07
Porcentaje completado: 99.07
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.07
No problem status. Obteniendo sopa
No problem status. Obteniendo

No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Porcentaje completado: 99.29
Porcentaje completado: 99.29
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.29
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.29
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Porcentaje completado: 99.29
Porcentaje completado: 99.3
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.3
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.31
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.31
Sopa obtenida
Porcentaje completado: 99.3
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.31
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.31
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje complet

Porcentaje completado: 99.52
Sopa obtenida
Porcentaje completado: 99.52
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.52
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.53
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.53
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.53
Sopa obtenida
Porcentaje completado: 99.53
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.54
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.54
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.54
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.54
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.54
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.55
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.75
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.76
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.76
Sopa obtenida
Porcentaje completado: 99.76
No problem status. Obteniendo sopa
Sopa obtenida
No problem status. Obteniendo sopa
Porcentaje completado: 99.77
Sopa obtenida
Porcentaje completado: 99.77
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.77
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.77
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.78
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.78
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 99.78
Sopa obtenida
Porcentaje completado: 99.78
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje comp

No problem status. Obteniendo sopaNo problem status. Obteniendo sopa

Sopa obtenida
Porcentaje completado: 100.0
Sopa obtenida
Porcentaje completado: 99.99
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 100.0
Sopa obtenida
Porcentaje completado: 100.0


In [87]:
# Lo ponemos en un df
atributos_sucursales_bruto_df = pd.DataFrame.from_records(data,
                                                    columns = ["id_sucursal",
                                                               "attributes",
                                                               "prices",
                                                               "opinions"])
# Revisemos que tal quedó
atributos_sucursales_bruto_df.head(3)

id_sucursal                                        attributes  \
0            0  [4.2, 450, 20 - 35 min, Gratis(nuevos usuarios)]   
1            1          [nan, nan, nan, Gratis(nuevos usuarios)]   
2            2  [nan, nan, 23 - 38 min, Gratis(nuevos usuarios)]   

                                              prices  \
0  [$ 520,00, $ 400,00, $ 400,00, $ 400,00, $ 650...   
1  [$ 177,00, $ 231,00, $ 177,00, $ 398,00, $ 362...   
2  [$ 1.210,00, $ 350,00, $ 510,00, $ 585,00, $ 5...   

                                            opinions  
0  [(Calidad de la comida, 27%), (Justo lo que pe...  
1                                                 []  
2                                                 []

## Revisión de últimos errores

Busquemos si queda algún error por allí. Por si acaso

In [180]:
atributos_sucursales_bruto_df[atributos_sucursales_bruto_df["opinions"] == "Error opiniones"]

id_sucursal          attributes            prices         opinions
1386          1386  Problema atributos  Problema precios  Error opiniones
1740          1740  Problema atributos  Problema precios  Error opiniones
3234          3234  Problema atributos  Problema precios  Error opiniones
3621          3621  Problema atributos  Problema precios  Error opiniones
4399          4399  Problema atributos  Problema precios  Error opiniones
...            ...                 ...               ...              ...
35455        35455  Problema atributos  Problema precios  Error opiniones
35896        35896  Problema atributos  Problema precios  Error opiniones
36161        36161  Problema atributos  Problema precios  Error opiniones
37916        37916  Problema atributos  Problema precios  Error opiniones
38547        38547  Problema atributos  Problema precios  Error opiniones

[65 rows x 4 columns]

In [181]:
# Retorna la lista de índices en donde se detectaron errores
revisar = atributos_sucursales_bruto_df[atributos_sucursales_bruto_df["opinions"] == "Error opiniones"].index
revisar

Int64Index([ 1386,  1740,  3234,  3621,  4399,  5544,  5545,  5795,  5937,
             5969,  6277,  6369,  6778,  7124,  8279,  8304,  8591,  9503,
            10055, 10299, 10532, 10789, 10794, 11552, 11555, 11564, 11566,
            11570, 11571, 11575, 11576, 11577, 11714, 11723, 12253, 12526,
            12541, 13102, 13220, 14840, 15311, 15548, 15585, 19153, 19174,
            19472, 19585, 27939, 29960, 30394, 30456, 30469, 30646, 30674,
            31678, 31997, 32225, 32613, 34271, 34760, 35455, 35896, 36161,
            37916, 38547],
           dtype='int64')

Veamos si podemos solucionarlo aplicando la función denuevo

In [182]:
# Reapliquemos 
all_index_sucursales = revisar

with concurrent.futures.ProcessPoolExecutor() as executor:
    results = executor.map(process_sucursal, all_index_sucursales)
    
# Guardamos la data
data = list(results)

No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 7.27
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 8.14
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.12
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 3.91
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 9.88
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 12.46
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 12.46
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 13.02
No problem status. Obteniendo sopa
No problem status. Obteniendo sopa
Sopa obtenida
Sopa obtenida
Porcentaje completado: 13.41
Porcentaje completado: 14.1
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 13.34
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado: 16.0
No problem status. Obteniendo sopa
Sopa obtenida
Porcentaje completado:

In [183]:
# Revisemos
atributos_sucursales_bruto_df_errores = pd.DataFrame.from_records(data,
                                                    columns = ["id_sucursal",
                                                               "attributes",
                                                               "prices",
                                                               "opinions"])
# Revisemos que tal quedó
atributos_sucursales_bruto_df_errores

id_sucursal                                        attributes  \
0          1386   [4.5, 71, 35 - 50 min, Gratis(nuevos usuarios)]   
1          1740  [4.5, 111, 35 - 50 min, Gratis(nuevos usuarios)]   
2          3234  [4.2, 911, 35 - 50 min, Gratis(nuevos usuarios)]   
3          3621  [nan, nan, 26 - 41 min, Gratis(nuevos usuarios)]   
4          4399   [4.7, 73, 35 - 50 min, Gratis(nuevos usuarios)]   
..          ...                                               ...   
60        35455           [nan, nan, nan, Grátis(novos usuários)]   
61        35896           [nan, nan, nan, Grátis(novos usuários)]   
62        36161           [nan, nan, nan, Grátis(novos usuários)]   
63        37916           [nan, nan, nan, Grátis(novos usuários)]   
64        38547           [nan, nan, nan, Grátis(novos usuários)]   

                                               prices  \
0   [S/ 91.90, S/ 70.90, S/ 39.90, S/ 69.90, S/ 49...   
1   [S/ 149.93, S/ 184.90, S/ 29.90, S/ 39.90, S/ ...   
2   [S/ 37.90, S/ 84.90, S/ 64.90, S/ 21.90, S/ 15...   
3   [S/ 20.00, S/ 38.00, S/ 38.00, S/ 48.00, S/ 48...   
4   [$ 229.00, $ 169.00, $ 149.00, $ 259.00, $ 179...   
..                                                ...   
60  [R$ 88,00, R$ 80,00, R$ 88,00, R$ 90,00, R$ 85...   
61  [R$ 65,98, R$ 28,99, R$ 41,99, R$ 19,99, R$ 25...   
62                                                 []   
63                                                 []   
64  [R$ 75,40, R$ 95,80, R$ 126,40, R$ 228,10, R$ ...   

                                             opinions  
0   [(Calidad de la comida, 38%), (Tal como lo ped...  
1   [(Calidad de la comida, 41%), (Tal como lo ped...  
2   [(Justo lo que pedí, 17%), (Tal como lo pedí, ...  
3                                                  []  
4   [(Justo lo que pedí, 23%), (Tal como lo pedí, ...  
..                                                ...  
60                                                 []  
61                                                 []  
62                                                 []  
63                                                 []  
64                                                 []  

[65 rows x 4 columns]

In [184]:
# Retorna la lista de índices en donde se detectaron errores (denuevo)
revisar_errores = atributos_sucursales_bruto_df_errores[atributos_sucursales_bruto_df_errores["opinions"] == "Error opiniones"].index
len(revisar_errores)

0

Bien, parece que nos decisimos de los deshicimos de los errores. Reemplazemos los nuevos valores nuevos por los anteriores malos

In [186]:
# Recambiemos con los datos buenos por los malos en el df original
for i, j in enumerate(atributos_sucursales_bruto_df_errores.id_sucursal):
    new_data = atributos_sucursales_bruto_df_errores[atributos_sucursales_bruto_df_errores["id_sucursal"] == j].loc[i,:]
    atributos_sucursales_bruto_df.iloc[j,:] = new_data

In [187]:
# Chequeamos que todo haya sido cambiado
atributos_sucursales_bruto_df.loc[revisar,:]

id_sucursal                                        attributes  \
1386          1386   [4.5, 71, 35 - 50 min, Gratis(nuevos usuarios)]   
1740          1740  [4.5, 111, 35 - 50 min, Gratis(nuevos usuarios)]   
3234          3234  [4.2, 911, 35 - 50 min, Gratis(nuevos usuarios)]   
3621          3621  [nan, nan, 26 - 41 min, Gratis(nuevos usuarios)]   
4399          4399   [4.7, 73, 35 - 50 min, Gratis(nuevos usuarios)]   
...            ...                                               ...   
35455        35455           [nan, nan, nan, Grátis(novos usuários)]   
35896        35896           [nan, nan, nan, Grátis(novos usuários)]   
36161        36161           [nan, nan, nan, Grátis(novos usuários)]   
37916        37916           [nan, nan, nan, Grátis(novos usuários)]   
38547        38547           [nan, nan, nan, Grátis(novos usuários)]   

                                                  prices  \
1386   [S/ 91.90, S/ 70.90, S/ 39.90, S/ 69.90, S/ 49...   
1740   [S/ 149.93, S/ 184.90, S/ 29.90, S/ 39.90, S/ ...   
3234   [S/ 37.90, S/ 84.90, S/ 64.90, S/ 21.90, S/ 15...   
3621   [S/ 20.00, S/ 38.00, S/ 38.00, S/ 48.00, S/ 48...   
4399   [$ 229.00, $ 169.00, $ 149.00, $ 259.00, $ 179...   
...                                                  ...   
35455  [R$ 88,00, R$ 80,00, R$ 88,00, R$ 90,00, R$ 85...   
35896  [R$ 65,98, R$ 28,99, R$ 41,99, R$ 19,99, R$ 25...   
36161                                                 []   
37916                                                 []   
38547  [R$ 75,40, R$ 95,80, R$ 126,40, R$ 228,10, R$ ...   

                                                opinions  
1386   [(Calidad de la comida, 38%), (Tal como lo ped...  
1740   [(Calidad de la comida, 41%), (Tal como lo ped...  
3234   [(Justo lo que pedí, 17%), (Tal como lo pedí, ...  
3621                                                  []  
4399   [(Justo lo que pedí, 23%), (Tal como lo pedí, ...  
...                                                  ...  
35455                                                 []  
35896                                                 []  
36161                                                 []  
37916                                                 []  
38547                                                 []  

[65 rows x 4 columns]

In [188]:
# Chequeamos por errores una última vez
revisar = atributos_sucursales_bruto_df[atributos_sucursales_bruto_df["opinions"] == "Error opiniones"].index
len(revisar)

0

Cool, con esto hecho, ordenamos nuestro df y lo envíamos

In [189]:
# Ordenamos el df
atributos_sucursales_bruto_df = atributos_sucursales_bruto_df.sort_values("id_sucursal")
# Lo guardamos
atributos_sucursales_bruto_df.to_csv("atributos_sucursales_bruto.csv", index=False)

Listo. Hasta aquí acabaría la en E en nuestro ETL, continua a la siguiente parte 'Transform' para conocer como seguimos desde aquí. Gracias por tu tiempo!